<h4>Obtener datos de canciones de AcousticBrainz según su recording_id</h4>

In [98]:
# Imports
import numpy as np
import pandas as pd
import requests
import time
import os

In [99]:
songs_with_data = pd.read_csv('not_processed_songs_part2.csv')
songs_with_data

C:\Users\USUARIO\AppData\Local\Temp\ipykernel_14660\757455040.py:1: DtypeWarning: Columns (76,77,78,79,80,81) have mixed types. Specify dtype option on import or set low_memory=False.
  songs_with_data = pd.read_csv('not_processed_songs_part2.csv')


Unnamed: 0.1  Unnamed: 0       artist_name                   song_name  \
0             39961     39961.0              nura          keiner hat gefragt   
1             39962     39962.0    nanci griffith   alabama soft spoken blues   
2             39963     39963.0    nanci griffith              michael's song   
3             39964     39964.0    nanci griffith  song for remembered heroes   
4             39965     39965.0    nanci griffith              west texas sun   
...             ...         ...               ...                         ...   
33654         73615     73615.0  michael w. smith              missing person   
33655         73616     73616.0  michael w. smith                love me good   
33656         73617     73617.0  michael w. smith               live the life   
33657         73618     73618.0  michael w. smith          never been unloved   
33658         73619     73619.0  michael w. smith        i believe in you now   

                               recording_id  danceable  not_danceable   male  \
0      b8616e2f-4045-4c05-8ec6-6b767292af2b        NaN            NaN    NaN   
1      37f15249-0f76-4845-b912-ac683757c200      0.031          0.969  0.099   
2      30dbb939-9dae-46ba-9867-449a9e9b8e5d      0.016          0.984  0.011   
3      ec2a8d8b-72a0-4cd2-a971-18e87e2f8946      0.016          0.984  0.006   
4      a5c25d62-58d9-4a7f-8128-c95e83aaa91b      0.023          0.977  0.080   
...                                     ...        ...            ...    ...   
33654  7041f123-f0d6-4db0-ac8c-a9ff5314f194        NaN            NaN    NaN   
33655  8ad3921f-3baa-4f4d-842c-37d6ae29c2d8        NaN            NaN    NaN   
33656  ba1466c4-ce37-47c8-b408-76e4500c4b21        NaN            NaN    NaN   
33657  cd5dca5d-907b-4bb1-b22f-28fc8c29b7bf        NaN            NaN    NaN   
33658  c587f11d-f031-463b-b975-31a95e832113        NaN            NaN    NaN   

       female  timbre_bright  ...  mood_mirex2  mood_mirex3  mood_mirex4  \
0         NaN            NaN  ...          NaN          NaN          NaN   
1       0.901          0.990  ...        0.317        0.429        0.115   
2       0.989          0.986  ...        0.314        0.441        0.128   
3       0.994          0.916  ...        0.073        0.738        0.126   
4       0.920          0.972  ...        0.185        0.603        0.093   
...       ...            ...  ...          ...          ...          ...   
33654     NaN            NaN  ...          NaN          NaN          NaN   
33655     NaN            NaN  ...          NaN          NaN          NaN   
33656     NaN            NaN  ...          NaN          NaN          NaN   
33657     NaN            NaN  ...          NaN          NaN          NaN   
33658     NaN            NaN  ...          NaN          NaN          NaN   

       mood_mirex5  artistsort        genre  releasecountry  albumartistsort  \
0              NaN         NaN          NaN             NaN              NaN   
1            0.044         NaN  ['Country']             NaN              NaN   
2            0.068         NaN  ['Country']             NaN              NaN   
3            0.019         NaN  ['Country']             NaN              NaN   
4            0.064         NaN  ['Country']             NaN              NaN   
...            ...         ...          ...             ...              ...   
33654          NaN         NaN          NaN             NaN              NaN   
33655          NaN         NaN          NaN             NaN              NaN   
33656          NaN         NaN          NaN             NaN              NaN   
33657          NaN         NaN          NaN             NaN              NaN   
33658          NaN         NaN          NaN             NaN              NaN   

           label  tracknumber  
0            NaN          NaN  
1      ['Philo']      ['2/9']  
2      ['Philo']      ['3/9']  
3      ['Philo']      ['4/9']  
4      ['Philo']      ['5/9']  
...    

In [101]:
# Get data from AcousticBrainz by recording_id
def get_data_by_recording_id(recording_id):
    url = f"https://acousticbrainz.org/{recording_id}/high-level"
    response = requests.get(url)

    if response.status_code == 200:
        data = response.json()
        return data
    else:
        print(f"  ⚠️ Error fetching data: {response.status_code}")

In [102]:
# Parameters
save_interval = 50
output_file = "../data/raw/more_songs_with_data.csv"
temp_file = output_file + ".temp"

# Counter variables to monitor the status of requests
total_requests = 0
rows_processed = 0
found_count = 0
not_found_count = 0

In [44]:
dataRoute = {
    "danceable" : "['highlevel']['danceability']['all']['danceable']",
    "not_danceable" : "['highlevel']['danceability']['all']['not_danceable']",
    "female" : "['highlevel']['gender']['all']['female']",
    "male" : "['highlevel']['gender']['all']['male']",
    "timbre_bright" : "['highlevel']['timbre']['all']['bright']",
    "timbre_dark" : "['highlevel']['timbre']['all']['dark']",
    "tonal" : "['highlevel']['tonal_atonal']['all']['tonal']",
    "atonal" : "['highlevel']['tonal_atonal']['all']['atonal']",
    "voice" : "['highlevel']['voice_instrumental']['all']['voice']",
    "instrumental" : "['highlevel']['voice_instrumental']['all']['instrumental']",

    "dortmund_alternative" : "['highlevel']['genre_dortmund']['all']['alternative']",
    "dortmund_blues" : "['highlevel']['genre_dortmund']['all']['blues']",
    "dortmund_electronic" : "['highlevel']['genre_dortmund']['all']['electronic']",
    "dortmund_folkcountry" : "['highlevel']['genre_dortmund']['all']['folkcountry']",
    "dortmund_funksoulrnb" : "['highlevel']['genre_dortmund']['all']['funksoulrnb']",
    "dortmund_jazz" : "['highlevel']['genre_dortmund']['all']['jazz']",
    "dortmund_pop" : "['highlevel']['genre_dortmund']['all']['pop']",
    "dortmund_raphiphop" : "['highlevel']['genre_dortmund']['all']['raphiphop']",
    "dortmund_rock" : "['highlevel']['genre_dortmund']['all']['rock']",

    "electronic_ambient" : "['highlevel']['genre_electronic']['all']['ambient']",
    "electronic_dnb" : "['highlevel']['genre_electronic']['all']['dnb']",
    "electronic_house" : "['highlevel']['genre_electronic']['all']['house']",
    "electronic_techno" : "['highlevel']['genre_electronic']['all']['techno']",
    "electronic_trance" : "['highlevel']['genre_electronic']['all']['trance']",

    "rosamerica_cla" : "['highlevel']['genre_rosamerica']['all']['cla']",
    "rosamerica_dan" : "['highlevel']['genre_rosamerica']['all']['dan']",
    "rosamerica_hip" : "['highlevel']['genre_rosamerica']['all']['hip']",
    "rosamerica_jaz" : "['highlevel']['genre_rosamerica']['all']['jaz']",
    "rosamerica_pop" : "['highlevel']['genre_rosamerica']['all']['pop']",
    "rosamerica_rhy" : "['highlevel']['genre_rosamerica']['all']['rhy']",
    "rosamerica_roc" : "['highlevel']['genre_rosamerica']['all']['roc']",
    "rosamerica_spe" : "['highlevel']['genre_rosamerica']['all']['spe']",

    "tzanetakis_blu" : "['highlevel']['genre_tzanetakis']['all']['blu']",
    "tzanetakis_cla" : "['highlevel']['genre_tzanetakis']['all']['cla']",
    "tzanetakis_cou" : "['highlevel']['genre_tzanetakis']['all']['cou']",
    "tzanetakis_dis" : "['highlevel']['genre_tzanetakis']['all']['dis']",
    "tzanetakis_hip" : "['highlevel']['genre_tzanetakis']['all']['hip']",
    "tzanetakis_jaz" : "['highlevel']['genre_tzanetakis']['all']['jaz']",
    "tzanetakis_met" : "['highlevel']['genre_tzanetakis']['all']['met']",
    "tzanetakis_pop" : "['highlevel']['genre_tzanetakis']['all']['pop']",
    "tzanetakis_reg" : "['highlevel']['genre_tzanetakis']['all']['reg']",
    "tzanetakis_roc" : "['highlevel']['genre_tzanetakis']['all']['roc']",

    "ismir04_rhythm_ChaChaCha" : "['highlevel']['ismir04_rhythm']['all']['ChaChaCha']",
    "ismir04_rhythm_Jive" : "['highlevel']['ismir04_rhythm']['all']['Jive']",
    "ismir04_rhythm_Quickstep" : "['highlevel']['ismir04_rhythm']['all']['Quickstep']",
    "ismir04_rhythm_Rumba-American" : "['highlevel']['ismir04_rhythm']['all']['Rumba-American']",
    "ismir04_rhythm_Rumba-International" : "['highlevel']['ismir04_rhythm']['all']['Rumba-International']",
    "ismir04_rhythm_Rumba-Misc" : "['highlevel']['ismir04_rhythm']['all']['Rumba-Misc']",
    "ismir04_rhythm_Samba" : "['highlevel']['ismir04_rhythm']['all']['Samba']",
    "ismir04_rhythm_Tango" : "['highlevel']['ismir04_rhythm']['all']['Tango']",
    "ismir04_rhythm_VienneseWaltz" : "['highlevel']['ismir04_rhythm']['all']['VienneseWaltz']",
    "ismir04_rhythm_Waltz" : "['highlevel']['ismir04_rhythm']['all']['Waltz']",

    "mood_acoustic" : "['highlevel']['mood_acoustic']['all']['acoustic']",
    "mood_not_acoustic" : "['highlevel']['mood_acoustic']['all']['not_acoustic']",
    "mood_aggressive" : "['highlevel']['mood_aggressive']['all']['aggressive']",
    "mood_not_aggressive" : "['highlevel']['mood_aggressive']['all']['not_aggressive']",
    "mood_electronic" : "['highlevel']['mood_electronic']['all']['electronic']",
    "mood_not_electronic" : "['highlevel']['mood_electronic']['all']['not_electronic']",
    "mood_happy" : "['highlevel']['mood_happy']['all']['happy']",
    "mood_not_happy" : "['highlevel']['mood_happy']['all']['not_happy']",
    "mood_party" : "['highlevel']['mood_party']['all']['party']",
    "mood_not_party" : "['highlevel']['mood_party']['all']['not_party']",
    "mood_relaxed" : "['highlevel']['mood_relaxed']['all']['relaxed']",
    "mood_not_relaxed" : "['highlevel']['mood_relaxed']['all']['not_relaxed']",
    "mood_sad" : "['highlevel']['mood_sad']['all']['sad']",
    "mood_not_sad" : "['highlevel']['mood_sad']['all']['not_sad']",
    "mood_mirex1" : "['highlevel']['moods_mirex']['all']['Cluster1']",
    "mood_mirex2" : "['highlevel']['moods_mirex']['all']['Cluster2']",
    "mood_mirex3" : "['highlevel']['moods_mirex']['all']['Cluster3']",
    "mood_mirex4" : "['highlevel']['moods_mirex']['all']['Cluster4']",
    "mood_mirex5" : "['highlevel']['moods_mirex']['all']['Cluster5']",
    "artistsort" : "['metadata']['tags']['artistsort']",
    "genre" : "['metadata']['tags']['genre']",
    "releasecountry" : "['metadata']['tags']['releasecountry']",
    "albumartistsort" : "['metadata']['tags']['albumartistsort']",
    "label" : "['metadata']['tags']['label']",
    "tracknumber" : "['metadata']['tags']['tracknumber']"
}

In [103]:
# Apply function for every row in the Dataset
for index in songs_with_data.index:
    recording_id = songs_with_data.loc[index, "recording_id"]

    # Check if we are receiving the recording_id and continue in any case
    if not recording_id:
        print(f"  ⚠️ Skipping row {index} - No recording_id found")
        continue

    # Count and monitor total request
    total_requests += 1
    rows_processed += 1
    print(f"\n[Progress] Request {total_requests}/{len(songs_with_data)}...")

    # Apply function
    data = get_data_by_recording_id(recording_id)

    # Check that data is not empty
    if not data:
        print(f"  ⚠️ No data found for recording_id: {recording_id}")
        not_found_count += 1
        continue

    print(f"  ✅ Data found for: {index}")
    found_count += 1

    for key, route in dataRoute.items():
        try:
            value_to_assign = data['highlevel']['danceability']['all']['danceable']
            if not isinstance(value_to_assign, (int, float)):
                value_to_assign = np.nan
            songs_with_data.loc[index, 'danceable'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for danceable")
            songs_with_data.loc[index, 'danceable'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing danceable: {e}")
            songs_with_data.loc[index, 'danceable'] = np.nan
        try:
            value_to_assign = data['highlevel']['danceability']['all'].get('not_danceable', np.nan)
            songs_with_data.loc[index, 'not_danceable'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for not_danceable")
            songs_with_data.loc[index, 'not_danceable'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing not_danceable: {e}")
            songs_with_data.loc[index, 'not_danceable'] = np.nan
        try:
            value_to_assign = data['highlevel']['gender']['all'].get('female', np.nan)
            songs_with_data.loc[index, 'female'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for female")
            songs_with_data.loc[index, 'female'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing female: {e}")
            songs_with_data.loc[index, 'female'] = np.nan
        try:
            value_to_assign = data['highlevel']['gender']['all'].get('male', np.nan)
            songs_with_data.loc[index, 'male'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for male")
            songs_with_data.loc[index, 'male'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing male: {e}")
            songs_with_data.loc[index, 'male'] = np.nan
        try:
            value_to_assign = data['highlevel']['timbre']['all'].get('bright', np.nan)
            songs_with_data.loc[index, 'timbre_bright'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for timbre_bright")
            songs_with_data.loc[index, 'timbre_bright'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing timbre_bright: {e}")
            songs_with_data.loc[index, 'timbre_bright'] = np.nan
        try:
            value_to_assign = data['highlevel']['timbre']['all'].get('dark', np.nan)
            songs_with_data.loc[index, 'timbre_dark'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for timbre_dark")
            songs_with_data.loc[index, 'timbre_dark'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing timbre_dark: {e}")
            songs_with_data.loc[index, 'timbre_dark'] = np.nan
        try:
            value_to_assign = data['highlevel']['tonal_atonal']['all'].get('tonal', np.nan)
            songs_with_data.loc[index, 'tonal'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for tonal")
            songs_with_data.loc[index, 'tonal'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing tonal: {e}")
            songs_with_data.loc[index, 'tonal'] = np.nan
        try:
            value_to_assign = data['highlevel']['tonal_atonal']['all'].get('atonal', np.nan)
            songs_with_data.loc[index, 'atonal'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for atonal")
            songs_with_data.loc[index, 'atonal'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing atonal: {e}")
            songs_with_data.loc[index, 'atonal'] = np.nan
        try:
            value_to_assign = data['highlevel']['voice_instrumental']['all'].get('voice', np.nan)
            songs_with_data.loc[index, 'voice'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for voice")
            songs_with_data.loc[index, 'voice'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing voice: {e}")
            songs_with_data.loc[index, 'voice'] = np.nan
        try:
            value_to_assign = data['highlevel']['voice_instrumental']['all'].get('instrumental', np.nan)
            songs_with_data.loc[index, 'instrumental'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for instrumental")
            songs_with_data.loc[index, 'instrumental'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing instrumental: {e}")
            songs_with_data.loc[index, 'instrumental'] = np.nan



        try:
            value_to_assign = data['highlevel']['genre_dortmund']['all'].get('alternative', np.nan)
            songs_with_data.loc[index, 'dortmund_alternative'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for dortmund_alternative")
            songs_with_data.loc[index, 'dortmund_alternative'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing dortmund_alternative: {e}")
            songs_with_data.loc[index, 'dortmund_alternative'] = np.nan
        try:
            value_to_assign = data['highlevel']['genre_dortmund']['all'].get('blues', np.nan)
            songs_with_data.loc[index, 'dortmund_blues'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for dortmund_blues")
            songs_with_data.loc[index, 'dortmund_blues'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing dortmund_blues: {e}")
            songs_with_data.loc[index, 'dortmund_blues'] = np.nan
        try:
            value_to_assign = data['highlevel']['genre_dortmund']['all'].get('electronic', np.nan)
            songs_with_data.loc[index, 'dortmund_electronic'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for dortmund_electronic")
            songs_with_data.loc[index, 'dortmund_electronic'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing dortmund_electronic: {e}")
            songs_with_data.loc[index, 'dortmund_electronic'] = np.nan
        try:
            value_to_assign = data['highlevel']['genre_dortmund']['all'].get('folkcountry', np.nan)
            songs_with_data.loc[index, 'dortmund_folkcountry'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for dortmund_folkcountry")
            songs_with_data.loc[index, 'dortmund_folkcountry'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing dortmund_folkcountry: {e}")
            songs_with_data.loc[index, 'dortmund_folkcountry'] = np.nan
        try:
            value_to_assign = data['highlevel']['genre_dortmund']['all'].get('funksoulrnb', np.nan)
            songs_with_data.loc[index, 'dortmund_funksoulrnb'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for dortmund_funksoulrnb")
            songs_with_data.loc[index, 'dortmund_funksoulrnb'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing dortmund_funksoulrnb: {e}")
            songs_with_data.loc[index, 'dortmund_funksoulrnb'] = np.nan
        try:
            value_to_assign = data['highlevel']['genre_dortmund']['all'].get('jazz', np.nan)
            songs_with_data.loc[index, 'dortmund_jazz'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for dortmund_jazz")
            songs_with_data.loc[index, 'dortmund_jazz'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing dortmund_jazz: {e}")
            songs_with_data.loc[index, 'dortmund_jazz'] = np.nan
        try:
            value_to_assign = data['highlevel']['genre_dortmund']['all'].get('pop', np.nan)
            songs_with_data.loc[index, 'dortmund_pop'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for dortmund_pop")
            songs_with_data.loc[index, 'dortmund_pop'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing dortmund_pop: {e}")
            songs_with_data.loc[index, 'dortmund_pop'] = np.nan
        try:
            value_to_assign = data['highlevel']['genre_dortmund']['all'].get('raphiphop', np.nan)
            songs_with_data.loc[index, 'dortmund_raphiphop'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for dortmund_raphiphop")
            songs_with_data.loc[index, 'dortmund_raphiphop'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing dortmund_raphiphop: {e}")
            songs_with_data.loc[index, 'dortmund_raphiphop'] = np.nan
        try:
            value_to_assign = data['highlevel']['genre_dortmund']['all'].get('rock', np.nan)
            songs_with_data.loc[index, 'dortmund_rock'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for dortmund_rock")
            songs_with_data.loc[index, 'dortmund_rock'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing dortmund_rock: {e}")
            songs_with_data.loc[index, 'dortmund_rock'] = np.nan



        try:
            value_to_assign = data['highlevel']['genre_electronic']['all'].get('ambient', np.nan)
            songs_with_data.loc[index, 'electronic_ambient'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for electronic_ambient")
            songs_with_data.loc[index, 'electronic_ambient'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing electronic_ambient: {e}")
            songs_with_data.loc[index, 'electronic_ambient'] = np.nan
        try:
            value_to_assign = data['highlevel']['genre_electronic']['all'].get('dnb', np.nan)
            songs_with_data.loc[index, 'electronic_dnb'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for electronic_dnb")
            songs_with_data.loc[index, 'electronic_dnb'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing electronic_dnb: {e}")
            songs_with_data.loc[index, 'electronic_dnb'] = np.nan
        try:
            value_to_assign = data['highlevel']['genre_electronic']['all'].get('house', np.nan)
            songs_with_data.loc[index, 'electronic_house'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for electronic_house")
            songs_with_data.loc[index, 'electronic_house'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing electronic_house: {e}")
            songs_with_data.loc[index, 'electronic_house'] = np.nan
        try:
            value_to_assign = data['highlevel']['genre_electronic']['all'].get('techno', np.nan)
            songs_with_data.loc[index, 'electronic_techno'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for electronic_techno")
            songs_with_data.loc[index, 'electronic_techno'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing electronic_techno: {e}")
            songs_with_data.loc[index, 'electronic_techno'] = np.nan
        try:
            value_to_assign = data['highlevel']['genre_electronic']['all'].get('trance', np.nan)
            songs_with_data.loc[index, 'electronic_trance'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for electronic_trance")
            songs_with_data.loc[index, 'electronic_trance'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing electronic_trance: {e}")
            songs_with_data.loc[index, 'electronic_trance'] = np.nan



        try:
            value_to_assign = data['highlevel']['genre_rosamerica']['all'].get('cla', np.nan)
            songs_with_data.loc[index, 'rosamerica_cla'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for rosamerica_cla")
            songs_with_data.loc[index, 'rosamerica_cla'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing rosamerica_cla: {e}")
            songs_with_data.loc[index, 'rosamerica_cla'] = np.nan
        try:
            value_to_assign = data['highlevel']['genre_rosamerica']['all'].get('dan', np.nan)
            songs_with_data.loc[index, 'rosamerica_dan'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for rosamerica_dan")
            songs_with_data.loc[index, 'rosamerica_dan'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing rosamerica_dan: {e}")
            songs_with_data.loc[index, 'rosamerica_dan'] = np.nan
        try:
            value_to_assign = data['highlevel']['genre_rosamerica']['all'].get('hip', np.nan)
            songs_with_data.loc[index, 'rosamerica_hip'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for rosamerica_hip")
            songs_with_data.loc[index, 'rosamerica_hip'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing rosamerica_hip: {e}")
            songs_with_data.loc[index, 'rosamerica_hip'] = np.nan
        try:
            value_to_assign = data['highlevel']['genre_rosamerica']['all'].get('jaz', np.nan)
            songs_with_data.loc[index, 'rosamerica_jaz'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for rosamerica_jaz")
            songs_with_data.loc[index, 'rosamerica_jaz'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing rosamerica_jaz: {e}")
            songs_with_data.loc[index, 'rosamerica_jaz'] = np.nan
        try:
            value_to_assign = data['highlevel']['genre_rosamerica']['all'].get('pop', np.nan)
            songs_with_data.loc[index, 'rosamerica_pop'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for rosamerica_pop")
            songs_with_data.loc[index, 'rosamerica_pop'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing rosamerica_pop: {e}")
            songs_with_data.loc[index, 'rosamerica_pop'] = np.nan
        try:
            value_to_assign = data['highlevel']['genre_rosamerica']['all'].get('rhy', np.nan)
            songs_with_data.loc[index, 'rosamerica_rhy'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for rosamerica_rhy")
            songs_with_data.loc[index, 'rosamerica_rhy'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing rosamerica_rhy: {e}")
            songs_with_data.loc[index, 'rosamerica_rhy'] = np.nan
        try:
            value_to_assign = data['highlevel']['genre_rosamerica']['all'].get('roc', np.nan)
            songs_with_data.loc[index, 'rosamerica_roc'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for rosamerica_roc")
            songs_with_data.loc[index, 'rosamerica_roc'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing rosamerica_roc: {e}")
            songs_with_data.loc[index, 'rosamerica_roc'] = np.nan
        try:
            value_to_assign = data['highlevel']['genre_rosamerica']['all'].get('spe', np.nan)
            songs_with_data.loc[index, 'rosamerica_spe'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for rosamerica_spe")
            songs_with_data.loc[index, 'rosamerica_spe'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing rosamerica_spe: {e}")
            songs_with_data.loc[index, 'rosamerica_spe'] = np.nan

        
        try:
            value_to_assign = data['highlevel']['genre_tzanetakis']['all'].get('blu', np.nan)
            songs_with_data.loc[index, 'tzanetakis_blu'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for tzanetakis_blu")
            songs_with_data.loc[index, 'tzanetakis_blu'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing tzanetakis_blu: {e}")
            songs_with_data.loc[index, 'tzanetakis_blu'] = np.nan
        try:
            value_to_assign = data['highlevel']['genre_tzanetakis']['all'].get('cla', np.nan)
            songs_with_data.loc[index, 'tzanetakis_cla'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for tzanetakis_cla")
            songs_with_data.loc[index, 'tzanetakis_cla'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing tzanetakis_cla: {e}")
            songs_with_data.loc[index, 'tzanetakis_cla'] = np.nan
        try:
            value_to_assign = data['highlevel']['genre_tzanetakis']['all'].get('cou', np.nan)
            songs_with_data.loc[index, 'tzanetakis_cou'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for tzanetakis_cou")
            songs_with_data.loc[index, 'tzanetakis_cou'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing tzanetakis_cou: {e}")
            songs_with_data.loc[index, 'tzanetakis_cou'] = np.nan
        try:
            value_to_assign = data['highlevel']['genre_tzanetakis']['all'].get('dis', np.nan)
            songs_with_data.loc[index, 'tzanetakis_dis'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for tzanetakis_dis")
            songs_with_data.loc[index, 'tzanetakis_dis'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing tzanetakis_dis: {e}")
            songs_with_data.loc[index, 'tzanetakis_dis'] = np.nan
        try:
            value_to_assign = data['highlevel']['genre_tzanetakis']['all'].get('hip', np.nan)
            songs_with_data.loc[index, 'tzanetakis_hip'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for tzanetakis_hip")
            songs_with_data.loc[index, 'tzanetakis_hip'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing tzanetakis_hip: {e}")
            songs_with_data.loc[index, 'tzanetakis_hip'] = np.nan
        try:
            value_to_assign = data['highlevel']['genre_tzanetakis']['all'].get('jaz', np.nan)
            songs_with_data.loc[index, 'tzanetakis_jaz'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for tzanetakis_jaz")
            songs_with_data.loc[index, 'tzanetakis_jaz'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing tzanetakis_jaz: {e}")
            songs_with_data.loc[index, 'tzanetakis_jaz'] = np.nan
        try:
            value_to_assign = data['highlevel']['genre_tzanetakis']['all'].get('met', np.nan)
            songs_with_data.loc[index, 'tzanetakis_met'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for tzanetakis_met")
            songs_with_data.loc[index, 'tzanetakis_met'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing tzanetakis_met: {e}")
            songs_with_data.loc[index, 'tzanetakis_met'] = np.nan
        try:
            value_to_assign = data['highlevel']['genre_tzanetakis']['all'].get('pop', np.nan)
            songs_with_data.loc[index, 'tzanetakis_pop'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for tzanetakis_pop")
            songs_with_data.loc[index, 'tzanetakis_pop'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing tzanetakis_pop: {e}")
            songs_with_data.loc[index, 'tzanetakis_pop'] = np.nan
        try:
            value_to_assign = data['highlevel']['genre_tzanetakis']['all'].get('reg', np.nan)
            songs_with_data.loc[index, 'tzanetakis_reg'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for tzanetakis_reg")
            songs_with_data.loc[index, 'tzanetakis_reg'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing tzanetakis_reg: {e}")
            songs_with_data.loc[index, 'tzanetakis_reg'] = np.nan
        try:
            value_to_assign = data['highlevel']['genre_tzanetakis']['all'].get('roc', np.nan)
            songs_with_data.loc[index, 'tzanetakis_roc'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for tzanetakis_roc")
            songs_with_data.loc[index, 'tzanetakis_roc'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing tzanetakis_roc: {e}")
            songs_with_data.loc[index, 'tzanetakis_roc'] = np.nan

        

        try:
            value_to_assign = data['highlevel']['ismir04_rhythm']['all'].get('ChaChaCha', np.nan)
            songs_with_data.loc[index, 'ismir04_rhythm_ChaChaCha'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for ismir04_rhythm_ChaChaCha")
            songs_with_data.loc[index, 'ismir04_rhythm_ChaChaCha'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing ismir04_rhythm_ChaChaCha: {e}")
            songs_with_data.loc[index, 'ismir04_rhythm_ChaChaCha'] = np.nan
        try:
            value_to_assign = data['highlevel']['ismir04_rhythm']['all'].get('Jive', np.nan)
            songs_with_data.loc[index, 'ismir04_rhythm_Jive'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for ismir04_rhythm_Jive")
            songs_with_data.loc[index, 'ismir04_rhythm_Jive'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing ismir04_rhythm_Jive: {e}")
            songs_with_data.loc[index, 'ismir04_rhythm_Jive'] = np.nan
        try:
            value_to_assign = data['highlevel']['ismir04_rhythm']['all'].get('Quickstep', np.nan)
            songs_with_data.loc[index, 'ismir04_rhythm_Quickstep'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for ismir04_rhythm_Quickstep")
            songs_with_data.loc[index, 'ismir04_rhythm_Quickstep'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing ismir04_rhythm_Quickstep: {e}")
            songs_with_data.loc[index, 'ismir04_rhythm_Quickstep'] = np.nan
        try:
            value_to_assign = data['highlevel']['ismir04_rhythm']['all'].get('Rumba-American', np.nan)
            songs_with_data.loc[index, 'ismir04_rhythm_Rumba-American'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for ismir04_rhythm_Rumba-American")
            songs_with_data.loc[index, 'ismir04_rhythm_Rumba-American'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing ismir04_rhythm_Rumba-American: {e}")
            songs_with_data.loc[index, 'ismir04_rhythm_Rumba-American'] = np.nan
        try:
            value_to_assign = data['highlevel']['ismir04_rhythm']['all'].get('Rumba-International', np.nan)
            songs_with_data.loc[index, 'ismir04_rhythm_Rumba-International'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for ismir04_rhythm_Rumba-International")
            songs_with_data.loc[index, 'ismir04_rhythm_Rumba-International'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing ismir04_rhythm_Rumba-International: {e}")
            songs_with_data.loc[index, 'ismir04_rhythm_Rumba-International'] = np.nan
        try:
            value_to_assign = data['highlevel']['ismir04_rhythm']['all'].get('Rumba-Misc', np.nan)
            songs_with_data.loc[index, 'ismir04_rhythm_Rumba-Misc'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for ismir04_rhythm_Rumba-Misc")
            songs_with_data.loc[index, 'ismir04_rhythm_Rumba-Misc'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing ismir04_rhythm_Rumba-Misc: {e}")
            songs_with_data.loc[index, 'ismir04_rhythm_Rumba-Misc'] = np.nan
        try:
            value_to_assign = data['highlevel']['ismir04_rhythm']['all'].get('Samba', np.nan)
            songs_with_data.loc[index, 'ismir04_rhythm_Samba'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for ismir04_rhythm_Samba")
            songs_with_data.loc[index, 'ismir04_rhythm_Samba'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing ismir04_rhythm_Samba: {e}")
            songs_with_data.loc[index, 'ismir04_rhythm_Samba'] = np.nan
        try:
            value_to_assign = data['highlevel']['ismir04_rhythm']['all'].get('Tango', np.nan)
            songs_with_data.loc[index, 'ismir04_rhythm_Tango'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for ismir04_rhythm_Tango")
            songs_with_data.loc[index, 'ismir04_rhythm_Tango'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing ismir04_rhythm_Tango: {e}")
            songs_with_data.loc[index, 'ismir04_rhythm_Tango'] = np.nan
        try:
            value_to_assign = data['highlevel']['ismir04_rhythm']['all'].get('VienneseWaltz', np.nan)
            songs_with_data.loc[index, 'ismir04_rhythm_VienneseWaltz'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for ismir04_rhythm_VienneseWaltz")
            songs_with_data.loc[index, 'ismir04_rhythm_VienneseWaltz'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing ismir04_rhythm_VienneseWaltz: {e}")
            songs_with_data.loc[index, 'ismir04_rhythm_VienneseWaltz'] = np.nan
        try:
            value_to_assign = data['highlevel']['ismir04_rhythm']['all'].get('Waltz', np.nan)
            songs_with_data.loc[index, 'ismir04_rhythm_Waltz'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for ismir04_rhythm_Waltz")
            songs_with_data.loc[index, 'ismir04_rhythm_Waltz'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing ismir04_rhythm_Waltz: {e}")
            songs_with_data.loc[index, 'ismir04_rhythm_Waltz'] = np.nan

        

        try:
            value_to_assign = data['highlevel']['mood_acoustic']['all'].get('acoustic', np.nan)
            songs_with_data.loc[index, 'mood_acoustic'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for mood_acoustic")
            songs_with_data.loc[index, 'mood_acoustic'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing mood_acoustic: {e}")
            songs_with_data.loc[index, 'mood_acoustic'] = np.nan
        try:
            value_to_assign = data['highlevel']['mood_acoustic']['all'].get('not_acoustic', np.nan)
            songs_with_data.loc[index, 'mood_not_acoustic'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for mood_not_acoustic")
            songs_with_data.loc[index, 'mood_not_acoustic'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing mood_not_acoustic: {e}")
            songs_with_data.loc[index, 'mood_not_acoustic'] = np.nan
        try:
            value_to_assign = data['highlevel']['mood_aggressive']['all'].get('aggressive', np.nan)
            songs_with_data.loc[index, 'mood_aggressive'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for mood_aggressive")
            songs_with_data.loc[index, 'mood_aggressive'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing mood_aggressive: {e}")
            songs_with_data.loc[index, 'mood_aggressive'] = np.nan
        try:
            value_to_assign = data['highlevel']['mood_aggressive']['all'].get('not_aggressive', np.nan)
            songs_with_data.loc[index, 'mood_not_aggressive'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for mood_not_aggressive")
            songs_with_data.loc[index, 'mood_not_aggressive'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing mood_not_aggressive: {e}")
            songs_with_data.loc[index, 'mood_not_aggressive'] = np.nan
        try:
            value_to_assign = data['highlevel']['mood_electronic']['all'].get('electronic', np.nan)
            songs_with_data.loc[index, 'mood_electronic'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for mood_electronic")
            songs_with_data.loc[index, 'mood_electronic'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing mood_electronic: {e}")
            songs_with_data.loc[index, 'mood_electronic'] = np.nan
        try:
            value_to_assign = data['highlevel']['mood_electronic']['all'].get('not_electronic', np.nan)
            songs_with_data.loc[index, 'mood_not_electronic'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for mood_not_electronic")
            songs_with_data.loc[index, 'mood_not_electronic'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing mood_not_electronic: {e}")
            songs_with_data.loc[index, 'mood_not_electronic'] = np.nan
        try:
            value_to_assign = data['highlevel']['mood_happy']['all'].get('happy', np.nan)
            songs_with_data.loc[index, 'mood_happy'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for mood_happy")
            songs_with_data.loc[index, 'mood_happy'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing mood_happy: {e}")
            songs_with_data.loc[index, 'mood_happy'] = np.nan
        try:
            value_to_assign = data['highlevel']['mood_happy']['all'].get('not_happy', np.nan)
            songs_with_data.loc[index, 'mood_not_happy'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for mood_not_happy")
            songs_with_data.loc[index, 'mood_not_happy'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing mood_not_happy: {e}")
            songs_with_data.loc[index, 'mood_not_happy'] = np.nan
        try:
            value_to_assign = data['highlevel']['mood_party']['all'].get('party', np.nan)
            songs_with_data.loc[index, 'mood_party'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for mood_party")
            songs_with_data.loc[index, 'mood_party'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing mood_party: {e}")
            songs_with_data.loc[index, 'mood_party'] = np.nan
        try:
            value_to_assign = data['highlevel']['mood_party']['all'].get('not_party', np.nan)
            songs_with_data.loc[index, 'mood_not_party'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for mood_not_party")
            songs_with_data.loc[index, 'mood_not_party'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing mood_not_party: {e}")
            songs_with_data.loc[index, 'mood_not_party'] = np.nan
        try:
            value_to_assign = data['highlevel']['mood_relaxed']['all'].get('relaxed', np.nan)
            songs_with_data.loc[index, 'mood_relaxed'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for mood_relaxed")
            songs_with_data.loc[index, 'mood_relaxed'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing mood_relaxed: {e}")
            songs_with_data.loc[index, 'mood_relaxed'] = np.nan
        try:
            value_to_assign = data['highlevel']['mood_relaxed']['all'].get('not_relaxed', np.nan)
            songs_with_data.loc[index, 'mood_not_relaxed'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for mood_not_relaxed")
            songs_with_data.loc[index, 'mood_not_relaxed'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing mood_not_relaxed: {e}")
            songs_with_data.loc[index, 'mood_not_relaxed'] = np.nan
        try:
            value_to_assign = data['highlevel']['mood_sad']['all'].get('sad', np.nan)
            songs_with_data.loc[index, 'mood_sad'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for mood_sad")
            songs_with_data.loc[index, 'mood_sad'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing mood_sad: {e}")
            songs_with_data.loc[index, 'mood_sad'] = np.nan
        try:
            value_to_assign = data['highlevel']['mood_sad']['all'].get('not_sad', np.nan)
            songs_with_data.loc[index, 'mood_not_sad'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for mood_not_sad")
            songs_with_data.loc[index, 'mood_not_sad'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing mood_not_sad: {e}")
            songs_with_data.loc[index, 'mood_not_sad'] = np.nan



        try:
            value_to_assign = data['highlevel']['moods_mirex']['all'].get('Cluster1', np.nan)
            songs_with_data.loc[index, 'mood_mirex1'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for mood_mirex1")
            songs_with_data.loc[index, 'mood_mirex1'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing mood_mirex1: {e}")
            songs_with_data.loc[index, 'mood_mirex1'] = np.nan
        try:
            value_to_assign = data['highlevel']['moods_mirex']['all'].get('Cluster2', np.nan)
            songs_with_data.loc[index, 'mood_mirex2'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for mood_mirex2")
            songs_with_data.loc[index, 'mood_mirex2'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing mood_mirex2: {e}")
            songs_with_data.loc[index, 'mood_mirex2'] = np.nan
        try:
            value_to_assign = data['highlevel']['moods_mirex']['all'].get('Cluster3', np.nan)
            songs_with_data.loc[index, 'mood_mirex3'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for mood_mirex3")
            songs_with_data.loc[index, 'mood_mirex3'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing mood_mirex3: {e}")
            songs_with_data.loc[index, 'mood_mirex3'] = np.nan
        try:
            value_to_assign = data['highlevel']['moods_mirex']['all'].get('Cluster4', np.nan)
            songs_with_data.loc[index, 'mood_mirex4'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for mood_mirex4")
            songs_with_data.loc[index, 'mood_mirex4'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing mood_mirex4: {e}")
            songs_with_data.loc[index, 'mood_mirex4'] = np.nan
        try:
            value_to_assign = data['highlevel']['moods_mirex']['all'].get('Cluster5', np.nan)
            songs_with_data.loc[index, 'mood_mirex5'] = round(value_to_assign, 3) if isinstance(value_to_assign, (int, float)) else value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for mood_mirex5")
            songs_with_data.loc[index, 'mood_mirex5'] = np.nan
        except Exception as e:
            print(f"⚠️ Error processing mood_mirex5: {e}")
            songs_with_data.loc[index, 'mood_mirex5'] = np.nan



        try:
            value_to_assign = data['metadata']['tags'].get('artistsort', None)
            songs_with_data.loc[index, 'artistsort'] = value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for artistsort")
            songs_with_data.loc[index, 'artistsort'] = None
        except Exception as e:
            print(f"⚠️ Error processing artistsort: {e}")
            songs_with_data.loc[index, 'artistsort'] = None
        try:
            value_to_assign = data['metadata']['tags'].get('genre', None)
            songs_with_data.loc[index, 'genre'] = value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for genre")
            songs_with_data.loc[index, 'genre'] = None
        except Exception as e:
            print(f"⚠️ Error processing genre: {e}")
            songs_with_data.loc[index, 'genre'] = None
        try:
            value_to_assign = data['metadata']['tags'].get('releasecountry', None)
            songs_with_data.loc[index, 'releasecountry'] = value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for releasecountry")
            songs_with_data.loc[index, 'releasecountry'] = None
        except Exception as e:
            print(f"⚠️ Error processing releasecountry: {e}")
            songs_with_data.loc[index, 'releasecountry'] = None
        try:
            value_to_assign = data['metadata']['tags'].get('albumartistsort', None)
            songs_with_data.loc[index, 'albumartistsort'] = value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for albumartistsort")
            songs_with_data.loc[index, 'albumartistsort'] = None
        except Exception as e:
            print(f"⚠️ Error processing albumartistsort: {e}")
            songs_with_data.loc[index, 'albumartistsort'] = None
        try:
            value_to_assign = data['metadata']['tags'].get('label', None)
            songs_with_data.loc[index, 'label'] = value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for label")
            songs_with_data.loc[index, 'label'] = None
        except Exception as e:
            print(f"⚠️ Error processing label: {e}")
            songs_with_data.loc[index, 'label'] = None
        try:
            value_to_assign = data['metadata']['tags'].get('tracknumber', None)
            songs_with_data.loc[index, 'tracknumber'] = value_to_assign
        except KeyError:
            print(f"⚠️ Missing key for tracknumber")
            songs_with_data.loc[index, 'tracknumber'] = None
        except Exception as e:
            print(f"⚠️ Error processing tracknumber: {e}")
            songs_with_data.loc[index, 'tracknumber'] = None


    # Print percentage of "Not found" vs valid IDs
    total_processed_so_far = found_count + not_found_count
    total_rows = len(songs_with_data)
    print(f"  [Stats] - Not Found: {not_found_count} Found: {found_count}")
    print(f"  [Stats] - Processed: {total_processed_so_far} / {total_rows}")

    # Save progress at intervals
    if rows_processed % save_interval == 0:
        try:
            print(f"Saving progress to temporary file: {temp_file}")
            songs_with_data.to_csv(temp_file, index=False)
        except Exception as e:
            print(f"Error saving file: {e}")

    # Respect the API rate limit
    time.sleep(1)


    # Final save after processing all rows
    try:
        print(f"Final save to file: {output_file}")
        os.rename(temp_file, output_file)  # Replace temporary file with final file
    except Exception as e:
        print(f"Error during final save: {e}")


[Progress] Request 1/33659...
  ⚠️ Error fetching data: 429
  ⚠️ No data found for recording_id: b8616e2f-4045-4c05-8ec6-6b767292af2b

[Progress] Request 2/33659...
  ⚠️ Error fetching data: 429
  ⚠️ No data found for recording_id: 37f15249-0f76-4845-b912-ac683757c200

[Progress] Request 3/33659...
  ⚠️ Error fetching data: 429
  ⚠️ No data found for recording_id: 30dbb939-9dae-46ba-9867-449a9e9b8e5d

[Progress] Request 4/33659...
  ⚠️ Error fetching data: 429
  ⚠️ No data found for recording_id: ec2a8d8b-72a0-4cd2-a971-18e87e2f8946

[Progress] Request 5/33659...
  ⚠️ Error fetching data: 429
  ⚠️ No data found for recording_id: a5c25d62-58d9-4a7f-8128-c95e83aaa91b

[Progress] Request 6/33659...
  ⚠️ Error fetching data: 404
  ⚠️ No data found for recording_id: 747a086f-6ad6-438b-b3c6-a3aaa247ed66

[Progress] Request 7/33659...
  ✅ Data found for: 6
  [Stats] - Not Found: 6 Found: 1
  [Stats] - Processed: 7 / 33659
Final save to file: ../data/raw/more_songs_with_data.csv
Error during 

KeyboardInterrupt: 

In [105]:
# Seleccionar los primeros 2091 registros
processed_data_songs = songs_with_data.head(20701)

# Guardar los datos procesados en un nuevo archivo CSV
processed_data_songs.to_csv('processed_data_songs.csv', index=False)

In [106]:
# Eliminar los primeros 2091 registros
remaining_data = songs_with_data.iloc[20701:]

# Guardar los datos restantes en el archivo original o en un nuevo archivo
remaining_data.to_csv('not_processed_songs_part2.csv', index=False)


In [107]:
data = pd.read_csv('not_processed_songs_part2.csv')
data

C:\Users\USUARIO\AppData\Local\Temp\ipykernel_14660\1359607365.py:1: DtypeWarning: Columns (76,77,78,79,80,81) have mixed types. Specify dtype option on import or set low_memory=False.
  data = pd.read_csv('not_processed_songs_part2.csv')


Unnamed: 0.1  Unnamed: 0       artist_name              song_name  \
0             60662     60662.0     tiffany evans       lay back & chill   
1             60663     60663.0     tiffany evans         girl gone wild   
2             60664     60664.0     tiffany evans            about a boy   
3             60665     60665.0     tiffany evans  favorite broken heart   
4             60666     60666.0     tiffany evans                  again   
...             ...         ...               ...                    ...   
12953         73615     73615.0  michael w. smith         missing person   
12954         73616     73616.0  michael w. smith           love me good   
12955         73617     73617.0  michael w. smith          live the life   
12956         73618     73618.0  michael w. smith     never been unloved   
12957         73619     73619.0  michael w. smith   i believe in you now   

                               recording_id  danceable  not_danceable   male  \
0      7b76f96b-fb39-4e0d-9616-e0f54eef7dba        NaN            NaN    NaN   
1      b365439b-8c81-41ce-82bb-49e19096c5b5      0.990          0.010  0.004   
2      2889b5cd-417f-4d36-b207-67e33e08e0d3      1.000          0.000  0.000   
3      0a033b45-b0bf-4521-9496-f71774c373e7      1.000          0.000  0.004   
4      c5049e29-28ba-4307-9963-69ac259101e5      0.999          0.001  0.005   
...                                     ...        ...            ...    ...   
12953  7041f123-f0d6-4db0-ac8c-a9ff5314f194        NaN            NaN    NaN   
12954  8ad3921f-3baa-4f4d-842c-37d6ae29c2d8        NaN            NaN    NaN   
12955  ba1466c4-ce37-47c8-b408-76e4500c4b21        NaN            NaN    NaN   
12956  cd5dca5d-907b-4bb1-b22f-28fc8c29b7bf        NaN            NaN    NaN   
12957  c587f11d-f031-463b-b975-31a95e832113        NaN            NaN    NaN   

       female  timbre_bright  ...  mood_mirex2  mood_mirex3  mood_mirex4  \
0         NaN            NaN  ...          NaN          NaN          NaN   
1       0.996          0.117  ...        0.089        0.360        0.209   
2       1.000          0.972  ...        0.345        0.178        0.195   
3       0.996          0.196  ...        0.092        0.397        0.195   
4       0.995          0.964  ...        0.449        0.159        0.219   
...       ...            ...  ...          ...          ...          ...   
12953     NaN            NaN  ...          NaN          NaN          NaN   
12954     NaN            NaN  ...          NaN          NaN          NaN   
12955     NaN            NaN  ...          NaN          NaN          NaN   
12956     NaN            NaN  ...          NaN          NaN          NaN   
12957     NaN            NaN  ...          NaN          NaN          NaN   

       mood_mirex5  artistsort    genre  releasecountry  albumartistsort  \
0              NaN         NaN      NaN             NaN              NaN   
1            0.269         NaN  ['R&B']             NaN              NaN   
2            0.142         NaN  ['R&B']             NaN              NaN   
3            0.245         NaN  ['R&B']             NaN              NaN   
4            0.072         NaN  ['R&B']             NaN              NaN   
...            ...         ...      ...             ...              ...   
12953          NaN         NaN      NaN             NaN              NaN   
12954          NaN         NaN      NaN             NaN              NaN   
12955          NaN         NaN      NaN             NaN              NaN   
12956          NaN         NaN      NaN             NaN              NaN   
12957          NaN         NaN      NaN             NaN              NaN   

       label  tracknumber  
0        NaN          NaN  
1        NaN        ['7']  
2        NaN        ['8']  
3        NaN        ['9']  
4        NaN       ['10']  
...      ...          ...  
12953    NaN          NaN  
12954    NaN          NaN  
12955    NaN          NaN  
12956    NaN          NaN  